# extract patient profiles from open-TCI dataset

In [19]:
import pandas as pd 
df = pd.read_csv('data.csv')
df.head()

@ID    TIME     CP       AMT    RATE  EVID  AGE    WT      HT  M1F2  A1V2
0    1  0.0000  0.000  39.39788  236.34     1   59  64.0  166.37     2     1
1    1  0.1667  0.000   8.82647   52.98     1   59  64.0  166.37     2     1
2    1  0.3333  0.000   3.92078   23.52     1   59  64.0  166.37     2     1
3    1  0.5000  0.000  15.07000   30.14     1   59  64.0  166.37     2     1
4    1  1.0000  6.932   0.00000    0.00     0   59  64.0  166.37     2     1

In [20]:
df_grouped = df.groupby('@ID')[['AGE', 'WT', 'HT', 'M1F2']].first()
df_grouped = df_grouped.reset_index()

In [22]:
df_grouped = df_grouped.rename(columns={'@ID': 'ID', 'M1F2':'Gender'})

In [24]:
df_grouped = df_grouped.round().astype(int)
df_grouped.Gender = df_grouped.Gender-1
df_grouped.head() 

ID  AGE   WT   HT  Gender
0   1   59   64  166       1
1   2   62   75  183       0
2   3   57  106  171       0
3   4   53   77  170       0
4   5   73   82  168       0

In [26]:
import plotly.express as px

fig = px.scatter_3d(df_grouped, x='WT', y='HT', z='AGE', color='Gender', 
                    color_discrete_map = {0:'blue',1:'red'}, hover_data=['ID'])

fig.update_layout(coloraxis_showscale=False, margin=dict(l=0, r=0, b=0, t=0))
fig.show()

In [34]:
def getProfileFromID(id):
    return df_grouped[df_grouped.ID==id].iloc[0, 1:].to_list()

In [43]:
# save df_grouped to csv
df_grouped.to_csv('profile_processed.csv', index=False)

# compare different patient profiles

- Inputs: patient profile, BIS trace with implusive noise, noise level
- Outputs: PID parameters

In [57]:
np.load("result.npy")['BIS'].shape

(7000,)

In [39]:
from fmpy import *
from fmpy import read_model_description, extract
from fmpy.fmi2 import FMU2Slave
import numpy as np
import shutil
import pandas as pd
import random
import plotly.graph_objects as go

In [40]:
derivative_control = False
input_noise = False
moving_average = False
output_noise = False
show_original = False

def simulation(id):
    profile = getProfileFromID(id)
    age = profile[0]
    weight = profile[1]
    height = profile[2]
    gender = profile[3]
    vrs = {}
    fmu = 'Pharmacokinetics_4_comportmental_model_PI_ref_FMU_base4_OAAS_lnx.fmu'
    model_description = read_model_description(fmu)
    for variable in model_description.modelVariables:
        vrs[variable.name] = variable.valueReference
    start_time = 0.0
    stop_time = 7000
    step_size = 1
    unzipdir = extract(fmu)
    fmu = FMU2Slave(guid=model_description.guid,
                    unzipDirectory=unzipdir,
                    modelIdentifier=model_description.coSimulation.modelIdentifier,
                    instanceName='instance1')

    # initialize
    fmu.instantiate()
    fmu.setupExperiment(startTime=start_time)
    fmu.enterInitializationMode()
    fmu.exitInitializationMode()

    fmu.setReal([vrs["amesim_interface.Age_year"]], [age])
    fmu.setReal([vrs["amesim_interface.BIS0"]], [95.6])
    fmu.setReal([vrs["amesim_interface.BISmin"]], [8.9])
    fmu.setReal([vrs["amesim_interface.Drug_concentration_mgmL"]], [20])
    fmu.setReal([vrs["amesim_interface.EC50"]], [2.23])
    fmu.setReal([vrs["amesim_interface.Gamma"]], [1.58])
    fmu.setReal([vrs["amesim_interface.Gender_0male_1female"]], [gender])
    fmu.setReal([vrs["amesim_interface.Height_cm"]], [height])
    fmu.setReal([vrs["amesim_interface.Infusion_rate_mLh"]], [200])
    fmu.setReal([vrs["amesim_interface.Weight_kg"]], [weight])
    vr_input = vrs["amesim_interface.Infusion_rate_mLh"]
    vr_output = vrs["amesim_interface.BIS_Index"]


    rows = []  # list to record the results
    time = start_time
    infusion_rate = 200
    i = 0
    target = 30
    last_error = 0
    last_bis = 0
    bis_history = []
    kp = 4
    ki = 0.01
    kd = kd if derivative_control else 0
    # simulation loop
    while time < stop_time:

        if time >= 2.4e3 and time < 4.5e3:
            target = 70
            p = 0
            i = 0
        if time >= 4.5e3:
            target = 30
            p = 0
            i = 0

        bis = fmu.getReal([int(vr_output)])[0] if time > step_size else 95.6
        if input_noise:
            bis += add_noise(min, max, std, mean)
        if moving_average:
            bis_history.append(bis)
            bis = bis if time <= window_size else np.mean(bis_history[-window_size:])
        p = bis - target
        i = i + p
        d = p - last_error
        last_error = p
        infusion_rate = np.clip(kp*p + ki*i + kd*d, 0, 200)
        if output_noise:
            infusion_rate += gen_pulsive_noise(time, min_pul, max_pul)
        
        fmu.setReal([vr_input], [int(infusion_rate)])
            
        # perform one step
        fmu.doStep(currentCommunicationPoint=time, communicationStepSize=step_size)

        # advance the time
        time += step_size
        # get the values for 'inputs' and 'outputs[4]'
        inputs, outputs = fmu.getReal([int(vr_input), int(vr_output)])

        # append the results
        rows.append((time, bis, inputs))

    fmu.terminate()
    fmu.freeInstance()
    shutil.rmtree(unzipdir, ignore_errors=True)
    result = np.array(rows, dtype=np.dtype([('time', np.float64), ('BIS', np.float64), ('Infusion', np.float64)]))
    df = pd.DataFrame(result)  
    df['ID'] = id
    return df

In [42]:
IDs = [6, 22]

df_all = pd.concat([simulation(id) for id in IDs])
fig1 = go.Figure()
for id in IDs:
    df_age = df_all[df_all['ID'] == id]
    fig1.add_trace(go.Scatter(x=df_age.index, y=df_age['BIS'], mode='lines', name=f'BIS for patient {id}'))

fig1.update_layout(height=400, width=1200, title_text="BIS evolution")
fig1.show()

fig2 = go.Figure()
for id in IDs:
    df_age = df_all[df_all['ID'] == id]
    fig2.add_trace(go.Scatter(x=df_age.index, y=df_age['Infusion'], mode='lines', name=f'Infusion rate for patient {id}'))

fig2.update_layout(height=400, width=1200, title_text="Infusion rate evolution")
fig2.show()

[WARNING] Pharmacokinetics_4_comportmental_model_PI_ref_FMU_base4_OAAS_fmi2Instantiate: the AME environment variable is undefined. Simulation could fail if the model requires datas from the Simcenter Amesim distribution
[WARNING] Pharmacokinetics_4_comportmental_model_PI_ref_FMU_base4_OAAS_fmi2Instantiate: the AME environment variable is undefined. Simulation could fail if the model requires datas from the Simcenter Amesim distribution


In [ ]:

def add_noise(min, max, std, mean):
        return np.clip(np.random.normal(mean, std), min, max)

def gen_pulsive_noise(count, min_val, max_val):
    pulse = 0
    n = count // 100  # Use integer division to get the floor of count / 100
    start = 100 * n
    end = start + 50
    if (count > start and count < end and n % 15 == 0):
        pulse = random.randint(min_val, max_val)
    
    return pulse
def simulation(input_noise, output_noise, min, max, std, mean, min_pul, max_pul, kd, show_original, derivative_control, moving_average, window_size):
    vrs = {}
    fmu = 'Pharmacokinetics_4_comportmental_model_PI_ref_FMU_base4_OAAS_lnx.fmu'
    model_description = read_model_description(fmu)
    for variable in model_description.modelVariables:
        vrs[variable.name] = variable.valueReference
    start_time = 0.0
    stop_time = 7000
    step_size = 1
    unzipdir = extract(fmu)

    fmu = FMU2Slave(guid=model_description.guid,
                    unzipDirectory=unzipdir,
                    modelIdentifier=model_description.coSimulation.modelIdentifier,
                    instanceName='instance1')

    # initialize
    fmu.instantiate()
    fmu.setupExperiment(startTime=start_time)
    fmu.enterInitializationMode()
    fmu.exitInitializationMode()

    fmu.setReal([vrs["amesim_interface.Age_year"]], [60])
    fmu.setReal([vrs["amesim_interface.BIS0"]], [95.6])
    fmu.setReal([vrs["amesim_interface.BISmin"]], [8.9])
    fmu.setReal([vrs["amesim_interface.Drug_concentration_mgmL"]], [20])
    fmu.setReal([vrs["amesim_interface.EC50"]], [2.23])
    fmu.setReal([vrs["amesim_interface.Gamma"]], [1.58])
    fmu.setReal([vrs["amesim_interface.Gender_0male_1female"]], [1])
    fmu.setReal([vrs["amesim_interface.Height_cm"]], [168])
    fmu.setReal([vrs["amesim_interface.Infusion_rate_mLh"]], [200])
    fmu.setReal([vrs["amesim_interface.Weight_kg"]], [75])
    vr_input = vrs["amesim_interface.Infusion_rate_mLh"]
    vr_output = vrs["amesim_interface.BIS_Index"]

    
    rows = []  # list to record the results
    time = start_time
    infusion_rate = 200
    i = 0
    target = 30
    last_error = 0
    last_bis = 0
    bis_history = []
    kp = 4
    ki = 0.01
    kd = kd if derivative_control else 0
    # simulation loop
    while time < stop_time:

        if time >= 2.4e3 and time < 4.5e3:
            target = 70
            p = 0
            i = 0
        if time >= 4.5e3:
            target = 30
            p = 0
            i = 0

        bis = fmu.getReal([int(vr_output)])[0] if time > step_size else 95.6
        if input_noise:
            bis += add_noise(min, max, std, mean)
        if moving_average:
            bis_history.append(bis)
            bis = bis if time <= window_size else np.mean(bis_history[-window_size:])
        p = bis - target
        i = i + p
        d = p - last_error
        last_error = p
        infusion_rate = np.clip(kp*p + ki*i + kd*d, 0, 200)
        if output_noise:
            infusion_rate += gen_pulsive_noise(time, min_pul, max_pul)
        
        fmu.setReal([vr_input], [int(infusion_rate)])
            
        # perform one step
        fmu.doStep(currentCommunicationPoint=time, communicationStepSize=step_size)

        # advance the time
        time += step_size
        # get the values for 'inputs' and 'outputs[4]'
        inputs, outputs = fmu.getReal([int(vr_input), int(vr_output)])

        # append the results
        rows.append((time, bis, inputs))

    fmu.terminate()
    fmu.freeInstance()
    shutil.rmtree(unzipdir, ignore_errors=True)
    result = np.array(rows, dtype=np.dtype([('time', np.float64), ('BIS', np.float64), ('Infusion', np.float64)]))
    df = pd.DataFrame(result)  
    trace1 = go.Scatter(x=df.index, y=df['BIS'], mode='lines', name='BIS')
    fig1 = go.Figure(data=trace1)
    fig1.update_layout(height=400, width=1200, title_text="BIS evolution")

    # Add a line trace for column_2 in the second subplot
    trace2 = go.Scatter(x=df.index, y=df['Infusion'], mode='lines', name='Infusion rate')
    fig2 = go.Figure(data=trace2)
    fig2.update_layout(height=400, width=1200, title_text="Infusion rate evolution")
    if show_original:
        if input_noise:
            result_baseline = np.load("result_gaussian.npy")
        elif output_noise:
            result_baseline = np.load("result_pulsive.npy")
        df_original = pd.DataFrame(result_baseline)
        fig1.add_trace(go.Scatter(x=df_original.index, y=df_original['BIS'], mode='lines', name='BIS original', line=dict(color="red"), opacity=0.5))
        fig2.add_trace(go.Scatter(x=df_original.index, y=df_original['Infusion'], mode='lines', name='Infusion rate original',  line=dict(color="red"), opacity=0.5))

    return fig1, fig2    

# add custom BIS target and noise

In [ ]:
from fmpy import *
from fmpy import read_model_description, extract
from fmpy.fmi2 import FMU2Slave
import numpy as np
import shutil
import pandas as pd
import random
import plotly.graph_objects as go
import json

df_profile = pd.read_csv("profile_processed.csv")
def getProfileFromID(id):
    return df_profile[df_profile.ID==id].iloc[0, 1:].to_list()

def simulation(id, kp, ki, kd, bis_target=40, min_noise=50, max_noise=150):
    profile = getProfileFromID(id)
    age = profile[0]
    weight = profile[1]
    height = profile[2]
    gender = profile[3]
    vrs = {}
    fmu = 'Pharmacokinetics_4_comportmental_model_PI_ref_FMU_base4_OAAS_lnx.fmu'
    model_description = read_model_description(fmu)
    for variable in model_description.modelVariables:
        vrs[variable.name] = variable.valueReference
    start_time = 0.0
    stop_time = 7000
    step_size = 1
    unzipdir = extract(fmu)

    fmu = FMU2Slave(guid=model_description.guid,
                    unzipDirectory=unzipdir,
                    modelIdentifier=model_description.coSimulation.modelIdentifier,
                    instanceName='instance1')

    # initialize
    fmu.instantiate()
    fmu.setupExperiment(startTime=start_time)
    fmu.enterInitializationMode()
    fmu.exitInitializationMode()

    fmu.setReal([vrs["amesim_interface.Age_year"]], [age])
    fmu.setReal([vrs["amesim_interface.BIS0"]], [95.6])
    fmu.setReal([vrs["amesim_interface.BISmin"]], [8.9])
    fmu.setReal([vrs["amesim_interface.Drug_concentration_mgmL"]], [20])
    fmu.setReal([vrs["amesim_interface.EC50"]], [2.23])
    fmu.setReal([vrs["amesim_interface.Gamma"]], [1.58])
    fmu.setReal([vrs["amesim_interface.Gender_0male_1female"]], [gender])
    fmu.setReal([vrs["amesim_interface.Height_cm"]], [height])
    fmu.setReal([vrs["amesim_interface.Infusion_rate_mLh"]], [200])
    fmu.setReal([vrs["amesim_interface.Weight_kg"]], [weight])
    vr_input = vrs["amesim_interface.Infusion_rate_mLh"]
    vr_output = vrs["amesim_interface.BIS_Index"]

    
    rows = []  # list to record the results
    time = start_time
    infusion_rate = 200
    i = 0
    target = bis_target
    last_error = 0
    # simulation loop
    impulsive_noise = random.randint(min_noise, max_noise)
    print("noise level:", impulsive_noise)
    while time < stop_time:

        if time >= 2.4e3 and time < 4.5e3:
            target = 70
            p = 0
            i = 0
        if time >= 4.5e3:
            target = bis_target
            p = 0
            i = 0

        bis = fmu.getReal([int(vr_output)])[0] if time > step_size else 95.6
        p = bis - target
        i = i + p
        d = p - last_error
        last_error = p
        infusion_rate = np.clip(kp*p + ki*i + kd*d, 0, 200)

        # add impulsive noise to infusion rate
        n = time // 100  
        start = 100 * n
        end = start + 50
        if (time > start and time < end and n % 15 == 0):
            infusion_rate += impulsive_noise
        
        fmu.setReal([vr_input], [int(infusion_rate)])
            
        # perform one step
        fmu.doStep(currentCommunicationPoint=time, communicationStepSize=step_size)

        # advance the time
        time += step_size
        # get the values for 'inputs' and 'outputs[4]'
        inputs, outputs = fmu.getReal([int(vr_input), int(vr_output)])

        # append the results
        rows.append((time, bis, inputs))

    fmu.terminate()
    fmu.freeInstance()
    shutil.rmtree(unzipdir, ignore_errors=True)
    result = np.array(rows, dtype=np.dtype([('time', np.float64), ('BIS', np.float64), ('Infusion', np.float64)]))
    return result, impulsive_noise

def plot_result(result, show_original): 
    df = pd.DataFrame(result)
    trace1 = go.Scatter(x=df.index, y=df['BIS'], mode='lines', name='BIS')
    fig1 = go.Figure(data=trace1)
    fig1.update_layout(height=400, width=1200, title_text="BIS evolution")

    # Add a line trace for column_2 in the second subplot
    trace2 = go.Scatter(x=df.index, y=df['Infusion'], mode='lines', name='Infusion rate')
    fig2 = go.Figure(data=trace2)
    fig2.update_layout(height=400, width=1200, title_text="Infusion rate evolution")
    if show_original:
        result_baseline = np.load("result_impulsive.npy")
        df_original = pd.DataFrame(result_baseline)
        fig1.add_trace(go.Scatter(x=df_original.index, y=df_original['BIS'], mode='lines', name='BIS original', line=dict(color="red"), opacity=0.5))
        fig2.add_trace(go.Scatter(x=df_original.index, y=df_original['Infusion'], mode='lines', name='Infusion rate original',  line=dict(color="red"), opacity=0.5))
    else: 
        np.save("result_impulsive.npy", result)
    return fig1, fig2  

def gradio_display_profile(id):
    profile = getProfileFromID(id)
    gender = "Male" if profile[3] == 0 else "Female"
    data = {}
    data["age"] = [profile[0]]
    data["weight"] = [profile[1]]
    data["height"] = [profile[2]]
    data["gender"] = [gender]
    df = pd.DataFrame(data)
    return df

def gradio_simulation(id, kp, ki, kd, show_original, bis_target, min_noise, max_noise):
    result, noise_level = simulation(id, kp, ki, kd, bis_target, min_noise, max_noise)
    fig1, fig2 = plot_result(result, show_original)
    return fig1, fig2, noise_level

def gradio_save(id, kp, ki, kd, bis_target, min_noise, max_noise):
    result, noise_level = simulation(id, kp, ki, kd, bis_target, min_noise, max_noise)
    patient_profile = getProfileFromID(id)


    # Assuming patient_profile is a list of 4 integers, bis_trace is a list of 7000 floats, and kp, ki, kd are floats
    data = {
        'inputs': {
            'patient_profile': {
                            'age': patient_profile[0],
                            'weight': patient_profile[1],
                            'height': patient_profile[2],
                            'gender': patient_profile[3]
                        },
            'bis_trace': result['BIS'].tolist(),
            'noise_level': noise_level
        },
        'outputs': {
            'kp': kp,
            'ki': ki,
            'kd': kd
        }
    }
    with open(f'saved_data/patient-{id}.json', 'w') as f:
        json.dump(data, f)
    return "Saved"


In [ ]:
gradio_save(0, 4, 0.01, 131, 40, 50, 150)

[WARNING] Pharmacokinetics_4_comportmental_model_PI_ref_FMU_base4_OAAS_fmi2Instantiate: the AME environment variable is undefined. Simulation could fail if the model requires datas from the Simcenter Amesim distribution
noise level: 65


'Saved'